# Working with Pandas II
Prepared by Dr. Kalpakis for CMSC 491/691, Fall 2017

In [1]:
import pandas as pd
import re
import random

## Reading a CSV using *pandas*

In [2]:
# Read the CSV into a dataframe. The CSV file is located at the same directory as the notebook file    
#frame = pd.read_csv("911_Calls_for_Service.csv", nrows=10000)
#frame.to_csv("911_Calls_for_Service_small.csv")
frame = pd.read_csv("911_Calls_for_Service_small.csv")

# make random sample of dataframe
frame = frame.sample(frac=0.25, replace=False)

## Peek at the head and tail of the data

In [3]:
# Show the first 5 and last 5 rows of the DF
frame.head(5)

Unnamed: 0            callDateTime priority district      description  \
5606        5606  07/15/2015 12:54:00 AM   Medium       SW       DISORDERLY   
3869        3869  07/14/2015 01:21:00 PM     High       SE  AUTO ACC/INJURY   
4010        4010  07/14/2015 09:22:00 PM   Medium       SD  JUV DISTURBANCE   
8165        8165  07/15/2015 06:57:00 PM   Medium       SE       DISORDERLY   
4630        4630  07/14/2015 05:20:00 PM   Medium       CD    911/NO  VOICE   

      callNumber          incidentLocation                  location  
5606  P151960095  W NORTH AV/N ROSEDALE ST    (39.308957,-76.669325)  
3869  P151951442            2700 BOSTON ST  (39.2796259,-76.5785027)  
4010  P151953234     BAY-BROOK ELEM MIDDLE    (39.226381,-76.599821)  
8165  P151962576        3400 BLK HUDSON ST  (39.2824920,-76.5687395)  
4630  P151952293         1000 CATHEDRAL ST  (39.3011812,-76.6180370)

In [4]:
frame.tail(5)

Unnamed: 0            callDateTime priority district    description  \
1708        1708  07/13/2015 07:13:00 PM   Medium       CD  911/NO  VOICE   
3788        3788  07/14/2015 01:47:00 PM   Medium       ED  911/NO  VOICE   
9768        9768  07/16/2015 10:03:00 AM      Low       NE       DOG BITE   
3687        3687  07/14/2015 12:19:00 PM      Low       ED      Transport   
823          823  07/13/2015 06:42:00 PM      Low       ED       BAIL OUT   

      callNumber           incidentLocation                  location  
1708  P151942795           600 E FAYETTE ST  (39.2906737,-76.6071600)  
3788  P151951521          600 N CAROLINE ST  (39.2971386,-76.5975453)  
9768  P151970829    MORAVIA PARK ELEMENTARY    (39.319454,-76.540329)  
3687  P151951222               300 N GAY ST  (39.2940575,-76.6081374)  
823   P151942693  E LAFAYETTE AV/N BROADWAY    (39.310655,-76.594903)

In [5]:
# get the shape (#rows, #cols) of the dataframe
print('(#rows,#cols)=', frame.shape)

#compute some basic statictics of tha data in each column
frame.describe()

(#rows,#cols)= (2500, 8)


Unnamed: 0
count  2500.000000
mean   4985.444800
std    2899.193284
min       4.000000
25%    2430.750000
50%    4943.000000
75%    7490.000000
max    9999.000000

## Data Preprocessing
Create a fresh copy of the data frame for editing keeping the original intact.

In [6]:
#make a copy of the dataframe
df = frame.copy()

In [7]:
#drop the callNumber column (axis=1)
df = df.drop(['callNumber'], axis=1)
df.tail(5)

Unnamed: 0            callDateTime priority district    description  \
1708        1708  07/13/2015 07:13:00 PM   Medium       CD  911/NO  VOICE   
3788        3788  07/14/2015 01:47:00 PM   Medium       ED  911/NO  VOICE   
9768        9768  07/16/2015 10:03:00 AM      Low       NE       DOG BITE   
3687        3687  07/14/2015 12:19:00 PM      Low       ED      Transport   
823          823  07/13/2015 06:42:00 PM      Low       ED       BAIL OUT   

               incidentLocation                  location  
1708           600 E FAYETTE ST  (39.2906737,-76.6071600)  
3788          600 N CAROLINE ST  (39.2971386,-76.5975453)  
9768    MORAVIA PARK ELEMENTARY    (39.319454,-76.540329)  
3687               300 N GAY ST  (39.2940575,-76.6081374)  
823   E LAFAYETTE AV/N BROADWAY    (39.310655,-76.594903)

In [8]:
#Let's take a look at the priority column
df['priority'].value_counts()

Medium           1280
Low               597
High              342
Non-Emergency     272
Emergency           1
Name: priority, dtype: int64

In [9]:
# extract multiple named regex groups from a column in a dataframe
dq = df['callDateTime'].str.extract('(?P<date>[\d]{2}/\d{2}/\d{4})\s(?P<time>\d{2}:\d{2}:\d{2}\s[AP]M)', expand=True)

#convert from between time formats
dq['time24'] = pd.to_datetime(dq['time']).dt.strftime('%H:%M:%S')
dq.tail(10)

date         time    time24
1615  07/13/2015  06:45:00 PM  18:45:00
9328  07/16/2015  04:03:00 AM  04:03:00
5768  07/16/2015  01:11:00 AM  01:11:00
9588  07/16/2015  08:56:00 AM  08:56:00
5275  07/14/2015  08:33:00 PM  20:33:00
1708  07/13/2015  07:13:00 PM  19:13:00
3788  07/14/2015  01:47:00 PM  13:47:00
9768  07/16/2015  10:03:00 AM  10:03:00
3687  07/14/2015  12:19:00 PM  12:19:00
823   07/13/2015  06:42:00 PM  18:42:00

In [10]:
# merge with original frame and keep the row index
df = df.reset_index() # move row index to a column named 'index'
dq = dq.reset_index() 
df = pd.merge(df, dq, how='left', on='index')
df.set_index('index', drop=True, inplace=True) # move the index column back to be row index
df.index.name = None
df.head(5)

Unnamed: 0            callDateTime priority district      description  \
5606        5606  07/15/2015 12:54:00 AM   Medium       SW       DISORDERLY   
3869        3869  07/14/2015 01:21:00 PM     High       SE  AUTO ACC/INJURY   
4010        4010  07/14/2015 09:22:00 PM   Medium       SD  JUV DISTURBANCE   
8165        8165  07/15/2015 06:57:00 PM   Medium       SE       DISORDERLY   
4630        4630  07/14/2015 05:20:00 PM   Medium       CD    911/NO  VOICE   

              incidentLocation                  location        date  \
5606  W NORTH AV/N ROSEDALE ST    (39.308957,-76.669325)  07/15/2015   
3869            2700 BOSTON ST  (39.2796259,-76.5785027)  07/14/2015   
4010     BAY-BROOK ELEM MIDDLE    (39.226381,-76.599821)  07/14/2015   
8165        3400 BLK HUDSON ST  (39.2824920,-76.5687395)  07/15/2015   
4630         1000 CATHEDRAL ST  (39.3011812,-76.6180370)  07/14/2015   

             time    time24  
5606  12:54:00 AM  00:54:00  
3869  01:21:00 PM  13:21:00  
4010  09:22:00 PM  21:22:00  
8165  06:57:00 PM  18:57:00  
4630  05:20:00 PM  17:20:00

In [11]:
df = df.drop('callDateTime',axis = 1)
df.head(5)

Unnamed: 0 priority district      description          incidentLocation  \
5606        5606   Medium       SW       DISORDERLY  W NORTH AV/N ROSEDALE ST   
3869        3869     High       SE  AUTO ACC/INJURY            2700 BOSTON ST   
4010        4010   Medium       SD  JUV DISTURBANCE     BAY-BROOK ELEM MIDDLE   
8165        8165   Medium       SE       DISORDERLY        3400 BLK HUDSON ST   
4630        4630   Medium       CD    911/NO  VOICE         1000 CATHEDRAL ST   

                      location        date         time    time24  
5606    (39.308957,-76.669325)  07/15/2015  12:54:00 AM  00:54:00  
3869  (39.2796259,-76.5785027)  07/14/2015  01:21:00 PM  13:21:00  
4010    (39.226381,-76.599821)  07/14/2015  09:22:00 PM  21:22:00  
8165  (39.2824920,-76.5687395)  07/15/2015  06:57:00 PM  18:57:00  
4630  (39.3011812,-76.6180370)  07/14/2015  05:20:00 PM  17:20:00

In [12]:
# Let's check if all entries in TIME are in the same format.
import re
pattern = r'[0-9]{2}:[0-9]{2}:[0-9]{2} (AM|PM)'
df['time'].str.match(pattern).unique()

array([ True], dtype=bool)

Lets add a new column showing which day of the week the call was placed.

In [13]:
df['weekday'] = df['date'].apply(lambda date: pd.Timestamp(date).weekday_name)
df['weekday'].value_counts()

Tuesday      812
Wednesday    763
Monday       605
Thursday     297
Sunday        10
Saturday       7
Friday         6
Name: weekday, dtype: int64

Knowing if it was dark or not at the time of call would give a good insight into the data.
That would depend on sunrise and sunset timings for a day which vary drastically. 
For simplicity, let's assume sunrise at 07:00 and sunset at 19:00

In [14]:
# drop the seconds (00) from the time
df['time'] = df['time'].str.replace(':00', '')
# extract the AM/PM indication in a separate column
df['apm'] = df['time'].str.extract('(AM|PM)', expand=True)

df['luminance'] = df['time24'].apply(lambda x:"light" if (x > '07:00:00' and x  < '19:00:00') else "dark")

df.head(5)

Unnamed: 0 priority district      description          incidentLocation  \
5606        5606   Medium       SW       DISORDERLY  W NORTH AV/N ROSEDALE ST   
3869        3869     High       SE  AUTO ACC/INJURY            2700 BOSTON ST   
4010        4010   Medium       SD  JUV DISTURBANCE     BAY-BROOK ELEM MIDDLE   
8165        8165   Medium       SE       DISORDERLY        3400 BLK HUDSON ST   
4630        4630   Medium       CD    911/NO  VOICE         1000 CATHEDRAL ST   

                      location        date      time    time24    weekday apm  \
5606    (39.308957,-76.669325)  07/15/2015  12:54 AM  00:54:00  Wednesday  AM   
3869  (39.2796259,-76.5785027)  07/14/2015  01:21 PM  13:21:00    Tuesday  PM   
4010    (39.226381,-76.599821)  07/14/2015  09:22 PM  21:22:00    Tuesday  PM   
8165  (39.2824920,-76.5687395)  07/15/2015  06:57 PM  18:57:00  Wednesday  PM   
4630  (39.3011812,-76.6180370)  07/14/2015  05:20 PM  17:20:00    Tuesday  PM   

     luminance  
5606      dark  
3869     light  
4010      dark  
8165     light  
4630     light

In [15]:
df['luminance'].value_counts()

light    1518
dark      982
Name: luminance, dtype: int64

Extract the latitude and longitude coordinates of the calls

In [16]:
df['latitude'] = df['location'].str.extract('(-?\d+.\d+)', expand=True)
df['longitude'] = df['location'].str.extract('-?\d+.\d+,(-?\d+.\d+)', expand=True)
df = df.drop(['location'], axis=1)
df.head(10)

Unnamed: 0       priority district      description  \
5606        5606         Medium       SW       DISORDERLY   
3869        3869           High       SE  AUTO ACC/INJURY   
4010        4010         Medium       SD  JUV DISTURBANCE   
8165        8165         Medium       SE       DISORDERLY   
4630        4630         Medium       CD    911/NO  VOICE   
3536        3536  Non-Emergency       WD     Foot  Patrol   
8059        8059         Medium       WD   COMMON ASSAULT   
9245        9245         Medium       ND       DISORDERLY   
8502        8502         Medium       NW   COMMON ASSAULT   
4929        4929         Medium       ND    911/NO  VOICE   

                     incidentLocation        date      time    time24  \
5606         W NORTH AV/N ROSEDALE ST  07/15/2015  12:54 AM  00:54:00   
3869                   2700 BOSTON ST  07/14/2015  01:21 PM  13:21:00   
4010            BAY-BROOK ELEM MIDDLE  07/14/2015  09:22 PM  21:22:00   
8165               3400 BLK HUDSON ST  07/15/2015  06:57 PM  18:57:00   
4630                1000 CATHEDRAL ST  07/14/2015  05:20 PM  17:20:00   
3536       W LAFAYETTE AV/N MONROE ST  07/14/2015  11:30 AM  11:30:00   
8059  GWYNNS FALLS PY/AUCHENTOROLY TE  07/15/2015  06:27 PM  18:27:00   
9245             OLD YORK RD/E 0TH ST  07/16/2015  02:55 AM  02:55:00   
8502              3700 GREENSPRING AV  07/15/2015  08:38 PM  20:38:00   
4929                     5200 YORK RD  07/14/2015  07:05 PM  19:05:00   

        weekday apm luminance    latitude    longitude  
5606  Wednesday  AM      dark   39.308957   -76.669325  
3869    Tuesday  PM     light  39.2796259  -76.5785027  
4010    Tuesday  PM      dark   39.226381   -76.599821  
8165  Wednesday  PM     light  39.2824920  -76.5687395  
4630    Tuesday  PM     light  39.3011812  -76.6180370  
3536    Tuesday  AM     light   39.298735   -76.647516  
8059  Wednesday  PM     light   39.318506   -76.647914  
9245   Thursday  AM      dark   39.335522   -76.607521  
8502  Wednesday  PM      dark  39.3322087  -76.6561007  
4929    Tuesday  PM      dark  39.3522360  -76.6105171

### Make some cross-tabulations

In [17]:
#make cross-tab of  priority and weekday
pd.crosstab(df.weekday, df.priority, margins=True)

priority   Emergency  High  Low  Medium  Non-Emergency   All
weekday                                                     
Friday             0     1    3       2              0     6
Monday             0    88  135     317             65   605
Saturday           0     2    1       3              1     7
Sunday             0     0    3       7              0    10
Thursday           1    39   76     150             31   297
Tuesday            0    97  197     418             93   805
Wednesday          0   115  182     383             82   762
All                1   342  597    1280            272  2492

In [18]:
ct = pd.crosstab([df.luminance, df.weekday], df.priority, margins=True)
ct.sort_index(axis=0, ascending=True)

priority             Emergency  High  Low  Medium  Non-Emergency   All
luminance weekday                                                     
All                          1   342  597    1280            272  2492
dark      Monday             0    28   37     109             19   193
          Saturday           0     0    0       0              1     1
          Sunday             0     0    3       7              0    10
          Thursday           0    17   29      63             18   127
          Tuesday            0    53   62     177             36   328
          Wednesday          0    58   70     148             40   316
light     Friday             0     1    3       2              0     6
          Monday             0    60   98     208             46   412
          Saturday           0     2    1       3              0     6
          Thursday           1    22   47      87             13   170
          Tuesday            0    44  135     241             57   477
          Wednesday          0    57  112     235             42   446

In [19]:
ct.sum()

priority
Emergency           2
High              684
Low              1194
Medium           2560
Non-Emergency     544
All              4984
dtype: int64

In [20]:
# find and remove duplicates
df.duplicated()

# transform data
data = pd.DataFrame({'food': ['bacon', 'pulled pork', 'bacon', 'Pastrami', 'corned beef', 'Bacon', 'pastrami', 'honey ham', 'nova lox'],
                  'ounces': [4, 3, 12, 6, 7.5, 8, 3, 5, 6]})
print(data)

# encode via a map
meat_to_animal = {
    'bacon': 'pig',
    'pulled pork': 'pig',
    'pastrami': 'cow',
    'corned beef': 'cow',
    'honey ham': 'pig',
    'nova lox': 'salmon'
}
data['animal'] = data['food'].map(str.lower).map(meat_to_animal)
data

          food  ounces
0        bacon     4.0
1  pulled pork     3.0
2        bacon    12.0
3     Pastrami     6.0
4  corned beef     7.5
5        Bacon     8.0
6     pastrami     3.0
7    honey ham     5.0
8     nova lox     6.0


food  ounces  animal
0        bacon     4.0     pig
1  pulled pork     3.0     pig
2        bacon    12.0     pig
3     Pastrami     6.0     cow
4  corned beef     7.5     cow
5        Bacon     8.0     pig
6     pastrami     3.0     cow
7    honey ham     5.0     pig
8     nova lox     6.0  salmon

### Discretization and Binning

In [21]:
ages = [20, 22, 25, 27, 21, 23, 37, 31, 61, 45, 41, 32]
bins = [18, 25, 35, 60, 100]
group_names = ['Youth', 'YoungAdult', 'MiddleAged', 'Senior'] # optional bin labels
# whether bin intervals are closed on the right
cats = pd.cut(ages, bins, labels=group_names, right=False)
cats

[Youth, Youth, YoungAdult, YoungAdult, Youth, ..., YoungAdult, Senior, MiddleAged, MiddleAged, YoungAdult]
Length: 12
Categories (4, object): [MiddleAged < Senior < YoungAdult < Youth]

In [22]:
#Other dataset https://catalog.data.gov/dataset/usda-national-nutrient-database-for-standard-reference-release-22